#**Progetto Spotify Youtube**

**Studente:** *Marco Sciacovelli*

**Materia:** *Piattaforme per i Big Data, Machine Learning*

**Professori:** *Prof. Luigi Laura, Prof.ssa Karolina Armonaite*

## Introduzione

Questo notebook ha lo scopo di fare un'analisi di un dataset con delle informazioni su alcune canzoni con i riferimenti alle piattaforme di Spotify e YouTube

L'idea è quella di andare a vedere quali sono gli artisti e le canzoni **più apprezzate** sulla piattaforma per poi cercare possibili **correlazioni** tra il tipo di canzone (valore di alcune metriche) e il numero di ascolti.

Il progetto si struttura in 7 fasi:
1. **Setting**, in cui vengono esplicitate le tecnologie utilizzate e fatto un setup della piattaforma scelta (Spark)
2. **Function**, in cui vengono definite tutte le funzioni (principalmente per la visualizzazione) che verranno utilizzate nel notebook e inserite in una sezione a parte per motivi di ordine e leggibilità del codice
3. **Import Data**, in cui vengono importati i dati
4. **Data Exploration**, in cui si inizia ad esplorare il dataset per coprenderne la struttura e il contenuto informativo. Questa sezione viene divisa in due, nella prima parte si farà un prima analisi usando Pandas su un subset del dataframe, solo successivamente si estenderà tutta l'analisi a tutto il dataset e si utilizzarà Spark.
5. **Data Cleaning e Manipulation**, in cui i dati verranno puliti e manipolati in modo da eliminare incoerenze, errori, valori nulli e raggiungere un formato corretto per l'analisi che vogliamo svolgere.
6. **Aggregation**, in cui si creeranno dei dataframe con delle informazioni aggregate a partire dalla tabella elaborata nel punto precedente
7. **Analysis and visualization**, in cui andremo effettivamente ad analizzare il dataset e visualizzare i risultati tramite grafici.

# Setting


In [ ]:
!apt-get install openjdk-8-jdk-headless -qq > /dev/null
!wget https://downloads.apache.org/spark/spark-3.5.3/spark-3.5.3-bin-hadoop3.tgz
!tar xf spark-3.5.3-bin-hadoop3.tgz
!pip install -q findspark

--2024-09-28 20:33:13--  https://downloads.apache.org/spark/spark-3.5.3/spark-3.5.3-bin-hadoop3.tgz
Resolving downloads.apache.org (downloads.apache.org)... 135.181.214.104, 88.99.208.237, 2a01:4f8:10a:39da::2, ...
Connecting to downloads.apache.org (downloads.apache.org)|135.181.214.104|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 400864419 (382M) [application/x-gzip]
Saving to: ‘spark-3.5.3-bin-hadoop3.tgz’

spark-3.5.3-bin-had 100%[===================>] 382.29M  5.58MB/s    in 73s     

2024-09-28 20:34:26 (5.25 MB/s) - ‘spark-3.5.3-bin-hadoop3.tgz’ saved [400864419/400864419]



In [ ]:
import os
import findspark

In [ ]:
os.environ["JAVA_HOME"]="/usr/lib/jvm/java-8-openjdk-amd64"
os.environ["SPARK_HOME"]="/content/spark-3.5.3-bin-hadoop3"

In [ ]:
findspark.init()

In [ ]:
import pyspark
from pyspark.sql import SparkSession

In [ ]:
spark = SparkSession.builder.master("local[*]").appName("Song analisys").getOrCreate()

In [ ]:
#versione stand alone
#!pip install pyspark

In [ ]:
#Import di tutte le librerie necessarie
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
import pyarrow as pa
from pyspark.sql.window import Window
import pyspark.sql.functions as f
from pyspark.sql.types import *
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import accuracy_score, classification_report

#Function

Definisco tutte le funzioni che verranno richiamate nelle sezioni successive

In [ ]:
#Funzione per creare un istogramma interattivo
def create_interactive_hist(dataframe, df_type, title, x_col,  y_col = None, color = 'blue'):

  #crea un grafico
  fig = go.Figure()

  #liste necessarie per il menù a tendina
  visibile = []
  for n in x_col:
    visibile.append(False)

  button_list = []

  #caso di un Pandas DataFrame
  if df_type == 'pandas':

    #aggiunge le diverse opzioni al grafico
    for idx, column in enumerate(x_col):
        fig.add_trace(go.Histogram(x=dataframe[column] , name=column,  marker=dict(color=color)))

        #creazione dei bottoni nel menù a tendina
        vis = visibile.copy()
        vis[idx] = True
        button_list.append(dict(label=column,
                        method="update",
                        args=[{"visible": vis},
                              {"title": title + ' - ' + column,
                                "xaxis": {"title": column},
                                "yaxis": {"title": 'Frequenza'}
                              }]))

  #caso di uno Spark Dataframe
  elif df_type == 'spark':

    #aggiunge le diverse opzioni al grafico
    for idx, column in enumerate(x_col):

      #creo la lista a partire dalla colonna
      x_val = dataframe.select(column).rdd.flatMap(lambda x: x).collect()

      fig.add_trace(go.Histogram(x=x_val, name=column, marker=dict(color=color)))

      #creazione dei bottoni nel menù a tendina
      vis = visibile.copy()
      vis[idx] = True
      button_list.append(dict(label=column,
                      method="update",
                      args=[{"visible": vis},
                              {"title": title + ' - ' + column,
                                "xaxis": {"title": column},
                                "yaxis": {"title": 'Frequenza'}
                              }]))

  #aggiunge il menu a tendina per selezionare la traccia da visualizzare
  fig.update_layout(
      updatemenus=[
          dict(
              buttons=button_list,
              direction="down",
          )
      ],
      #imposta un titolo predefinito per la prima visualizzazione
        title=title + ' - ' + x_col[0],
        xaxis_title=x_col[0],
        yaxis_title='Frequenza'
  )

  #imposta la visibilità predefinita per la prima visualizzazione
  fig.update_traces(visible=False)
  fig.data[0].visible = True
  fig.show()

In [ ]:
#Funzione per creare un grafico a barre interattivo
def create_interactive_bar(dataframe, x_col, y_col, title, color):

  #crea un grafico
  fig = go.Figure()

  for ax_col in x_col:

    #liste necessarie per il menù a tendina
    visibile = []
    for n in y_col:
      visibile.append(False)

    button_list = []

    #aggiunge le diverse opzioni al grafico
    for idx, column in enumerate(y_col):

        #prendo solo i 10 con valore più alto di 'column'
        df_bar = dataframe.sort_values(column, ascending = False).head(10)

        fig.add_trace(go.Bar(x=df_bar[ax_col], y=df_bar[column], name=column, marker=dict(color=color)))

        #creazione dei bottoni nel menù a tendina
        vis = visibile.copy()
        vis[idx] = True
        button_list.append(dict(label=column,
                        method="update",
                        args=[{"visible": vis},
                              {"title": title,
                                "xaxis": {"title": ax_col},
                                "yaxis": {"title": column}
                              }]))

    #aggiunge il menù a tendina per selezionare la traccia da visualizzare
    fig.update_layout(
        updatemenus=[
            dict(
                buttons=button_list,
                direction="down",
            )
        ],
        #imposta un titolo predefinito per la prima visualizzazione
        title=title,
        xaxis_title=ax_col,
        yaxis_title=y_col[0]
    )

    #imposta la visibilità predefinita per la prima visualizzazione
    fig.update_traces(visible=False)
    fig.data[0].visible = True
    fig.show()

In [ ]:
#Funzione per creare uno scatter plot interattivo
def create_interactive_scat(dataframe, x_col, y_col, title, color):

  #crea un grafico
  fig = go.Figure()

  for ax_col in x_col:

    #liste necessarie per il menù a tendina
    visibile = []
    for n in y_col:
      visibile.append(False)

    button_list = []

    #aggiunge le diverse opzioni al grafico
    for idx, column in enumerate(y_col):

        #prendo solo i 500 con valore più alto di 'ax_col'
        df_scat = dataframe.drop_duplicates(['Track', ax_col]).sort_values(ax_col, ascending = False).head(500)

        fig.add_trace(go.Scatter(x=df_scat[ax_col], y=df_scat[column], name=column, marker=dict(color=color),  mode='markers'))

        #creazione dei bottoni nel menù a tendina
        vis = visibile.copy()
        vis[idx] = True
        button_list.append(dict(
            label=column,
            method="update",
            args=[
                {"visible": vis},
                {
                    "title": title + ' - ' + ax_col,
                    "xaxis": {"title": ax_col},
                    "yaxis": {"title": column}
                }
            ]
        ))

    #aggiunge il menù a tendina per selezionare la traccia da visualizzare
    fig.update_layout(
        updatemenus=[
            dict(
                buttons=button_list,
                direction="down",
            )
        ],
        #imposta un titolo predefinito per la prima visualizzazione
        title=title + ' - ' + ax_col,
        xaxis_title=ax_col,
        yaxis_title=y_col[0]
    )

    #imposta la visibilità predefinita per la prima visualizzazione
    fig.update_traces(visible=False)
    fig.data[0].visible = True
    fig.show()

In [ ]:
def create_interactive_boxplot(dataframe, y_columns, x_col, title):

  #crea un grafico
  fig = go.Figure()

  #liste necessarie per il menù a tendina
  visibile = []
  for n in y_columns:
    visibile.append(False)

  buttons = []

  #aggiunge le diverse opzioni al grafico
  for idx, y_col in enumerate(y_columns):
      fig.add_trace(go.Box(
          x=dataframe[x_col],
          y=dataframe[y_col],
          name=y_col,
          boxmean='sd'
      ))

      #creazione dei bottoni nel menù a tendina
      vis = visibile.copy()
      vis[idx] = True
      buttons.append(dict(
          label=y_col,
          method='update',
          args=[{'visible': vis},
                {'title': title,
                 "xaxis": {"title": x_col},
                  "yaxis": {"title": y_col}
                }]
      ))

  #aggiunge il menù a tendina per selezionare la traccia da visualizzare
  fig.update_layout(
      title=title,
      xaxis_title=x_col,
      yaxis_title=y_columns[0],
      updatemenus=[
          dict(
              type='dropdown',
              buttons=buttons,
              direction='down',
              showactive=True,
          )
      ]
  )

  #imposta la visibilità predefinita per la prima visualizzazione
  fig.update_traces(visible=False)
  fig.data[0].visible = True
  fig.show()


In [ ]:
def random_forest(dataframe, feature_list, target):

  features = dataframe[feature_list]
  target = dataframe[target]

  X_train, X_test, y_train, y_test = train_test_split(features, target, test_size=0.2, random_state=42)

  # Inizializziamo il modello
  model = RandomForestClassifier(n_estimators=100, random_state=42)

  # Addestriamo il modello
  model.fit(X_train, y_train)


  # Previsioni
  y_pred = model.predict(X_test)

  # Accuratezza
  accuracy = accuracy_score(y_test, y_pred)
  print(f'Accuratezza: {accuracy} \n')

  # Report dettagliato della classificazione
  print(classification_report(y_test, y_pred))

# Import data

Inizialmente scarichiamo il file da Kaggle (riferimento: https://www.kaggle.com/datasets/salvatorerastelli/spotify-and-youtube), inizialmente sarà un csv zippato, quindi per prima cosa si unzippa.
Successivamente andremo a leggerlo sia come DataFrame Spark che Pandas.

Il dataframe contiene 27 variabili per ciascuna delle canzoni raccolte da Spotify, esse sono:

**Track**: nome della canzone, come visibile sulla piattaforma Spotify.  
**Artist**: nome dell'artista.  
**Url_spotify**: l'URL dell'artista.  
**Album**: l'album in cui la canzone è contenuta su Spotify.  
**Album_type**: indica se la canzone è stata pubblicata su Spotify come singolo o contenuta in un album.  
**Uri**: un link di Spotify usato per trovare la canzone tramite l'API.  
**Danceability**: descrive quanto una traccia sia adatta per ballare in base a una combinazione di elementi musicali tra cui tempo, stabilità del ritmo, forza del battito e regolarità generale. Un valore di 0.0 è il meno ballabile e 1.0 il più ballabile.  
**Energy**: è una misura da 0.0 a 1.0 e rappresenta una misura percettiva di intensità e attività. Tipicamente, le tracce energetiche sembrano veloci, rumorose e intense. Le caratteristiche percettive che contribuiscono a questo attributo includono gamma dinamica, volume percepito, timbro, tasso di attacco e entropia generale.  
**Key**: la tonalità in cui si trova la traccia. I numeri interi si riferiscono alle note utilizzando la notazione standard Pitch Class. Se non è stata rilevata alcuna tonalità, il valore è -1.  
**Loudness**: il volume complessivo di una traccia in decibel (dB). I valori di volume sono mediati su tutta la traccia e sono utili per confrontare il volume relativo delle tracce. Il volume è la qualità di un suono che è il principale correlato psicologico della forza fisica (ampiezza). I valori generalmente variano tra -60 e 0 dB.  
**Speechiness**: rileva la presenza di parole parlate in una traccia. Più la registrazione è esclusivamente simile a un discorso più il valore dell'attributo si avvicina a 1.0. Valori superiori a 0.66 descrivono tracce che probabilmente sono composte interamente da parole parlate. Valori tra 0.33 e 0.66 descrivono tracce che possono contenere sia musica che discorso, in sezioni o sovrapposti. Valori inferiori a 0.33 rappresentano molto probabilmente musica e altre tracce non simili a discorsi.  
**Acousticness**: una misura di confidenza da 0.0 a 1.0 che indica se la traccia è acustica. 1.0 rappresenta alta confidenza che la traccia sia acustica.  
**Instrumentalness**: predice se una traccia non contiene voci. I suoni "Ooh" e "Aah" sono trattati come strumentali in questo contesto. Più il valore di instrumentalness si avvicina a 1.0, maggiore è la probabilità che la traccia non contenga contenuto vocale. Valori superiori a 0.5 rappresentano tracce strumentali, ma la confidenza aumenta man mano che il valore si avvicina a 1.0.

**Liveness**: rileva la presenza di un pubblico nella registrazione. Valori di liveness più alti rappresentano una maggiore probabilità che la traccia sia stata eseguita dal vivo. Un valore superiore a 0.8 indica una forte probabilità che la traccia sia dal vivo.  
**Valence**: una misura da 0.0 a 1.0 che descrive la positività musicale trasmessa da una traccia. Le tracce con alta valence suonano più positive (ad esempio felici, allegre, euforiche), mentre le tracce con bassa valence suonano più negative (ad esempio tristi, depresse, arrabbiate).  
**Tempo**: il tempo complessivo stimato di una traccia in battiti per minuto (BPM). In terminologia musicale, il tempo è la velocità o il ritmo di un pezzo dato e deriva direttamente dalla durata media del battito.  
**Duration_ms**: la durata della traccia in millisecondi.  
**Stream**: numero di ascolti della canzone su Spotify.  
**Url_youtube**: URL del video collegato alla canzone su YouTube, se presente.  
**Title**: titolo del videoclip su YouTube.  
**Channel**: nome del canale che ha pubblicato il video.  
**Views**: numero di visualizzazioni.  
**Likes**: numero di "mi piace".  
**Comments**: numero di commenti.  
**Description**: descrizione del video su YouTube.  
**Licensed**: indica se il video rappresenta contenuti con licenza, il che significa che il contenuto è stato caricato su un canale collegato a un partner di contenuti di YouTube e poi rivendicato da quel partner.  
**official_video**: valore booleano che indica se il video trovato è il video ufficiale della canzone.

In [ ]:
#Scarichiamo il file

!kaggle datasets download -d salvatorerastelli/spotify-and-youtube

Dataset URL: https://www.kaggle.com/datasets/salvatorerastelli/spotify-and-youtube
License(s): CC0-1.0
 89% 8.00M/8.95M [00:01<00:00, 12.6MB/s]
100% 8.95M/8.95M [00:01<00:00, 8.31MB/s]


In [ ]:
#Unzip del file

!unzip '/content/spotify-and-youtube.zip'

Archive:  /content/spotify-and-youtube.zip
  inflating: Spotify_Youtube.csv     


In [ ]:
#Leggiamo il csv come uno Spark DataFrame, tutte le opzioni sono state aggiunte al fine di avere una corretta formattazione del df

df = spark.read.\
  option("header", "true").\
  option("inferSchema", "true").\
  option("multiLine", "true").\
  option("escape", "\"").\
  option("sep", ",").\
  option("lineSep", "\r\n").\
  csv('/content/Spotify_Youtube.csv')


In [ ]:
df.show(truncate=False)

+---+---------------------+------------------------------------------------------+---------------------------------------------------------------+---------------------------------------------------------------+----------+------------------------------------+------------+------+----+--------+-----------+------------+----------------+--------+-------+-------+-----------+-------------------------------------------+-----------------------------------------------------------------------------------------+---------------------+-------------+---------+--------+--------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

In [ ]:
df_pandas = pd.read_csv('/content/Spotify_Youtube.csv')

In [ ]:
df_pandas.head(20)

Unnamed: 0                 Artist  \
0            0               Gorillaz   
1            1               Gorillaz   
2            2               Gorillaz   
3            3               Gorillaz   
4            4               Gorillaz   
5            5               Gorillaz   
6            6               Gorillaz   
7            7               Gorillaz   
8            8               Gorillaz   
9            9               Gorillaz   
10          10  Red Hot Chili Peppers   
11          11  Red Hot Chili Peppers   
12          12  Red Hot Chili Peppers   
13          13  Red Hot Chili Peppers   
14          14  Red Hot Chili Peppers   
15          15  Red Hot Chili Peppers   
16          16  Red Hot Chili Peppers   
17          17  Red Hot Chili Peppers   
18          18  Red Hot Chili Peppers   
19          19  Red Hot Chili Peppers   

                                          Url_spotify  \
0   https://open.spotify.com/artist/3AA28KZvwAUcZu...   
1   https://open.spotify.com/artist/3AA28KZvwAUcZu...   
2   https://open.spotify.com/artist/3AA28KZvwAUcZu...   
3   https://open.spotify.com/artist/3AA28KZvwAUcZu...   
4   https://open.spotify.com/artist/3AA28KZvwAUcZu...   
5   https://open.spotify.com/artist/3AA28KZvwAUcZu...   
6   https://open.spotify.com/artist/3AA28KZvwAUcZu...   
7   https://open.spotify.com/artist/3AA28KZvwAUcZu...   
8   https://open.spotify.com/artist/3AA28KZvwAUcZu...   
9   https://open.spotify.com/artist/3AA28KZvwAUcZu...   
10  https://open.spotify.com/artist/0L8ExT028jH3dd...   
11  https://open.spotify.com/artist/0L8ExT028jH3dd...   
12  https://open.spotify.com/artist/0L8ExT028jH3dd...   
13  https://open.spotify.com/artist/0L8ExT028jH3dd...   
14  https://open.spotify.com/artist/0L8ExT028jH3dd...   
15  https://open.spotify.com/artist/0L8ExT028jH3dd...   
16  https://open.spotify.com/artist/0L8ExT028jH3dd...   
17  https://open.spotify.com/artist/0L8ExT028jH3dd...   
18  https://open.spotify.com/artist/0L8ExT028jH3dd...   
19  https://open.spotify.com/artist/0L8ExT028jH3dd...   

                                                Track  \
0                                      Feel Good Inc.   
1                                     Rhinestone Eyes   
2       New Gold (feat. Tame Impala and Bootie Brown)   
3                                  On Melancholy Hill   
4                                      Clint Eastwood   
5                                                DARE   
6   New Gold (feat. Tame Impala and Bootie Brown) ...   
7                  She's My Collar (feat. Kali Uchis)   
8                   Cracker Island (feat. Thundercat)   
9                                         Dirty Harry   
10                                    Californication   
11                                   Under the Bridge   
12                                         Can't Stop   
13                                        Scar Tissue   
14                                          Otherside   
15                                      Snow (Hey Oh)   
16                                    Dani California   
17                                         By the Way   
18                                       Give It Away   
19                                   Dark Necessities   

                                                Album Album_type  \
0                                          Demon Days      album   
1                                       Plastic Beach      album   
2       New Gold (feat. Tame Impala and Bootie Brown)     single   
3                                       Plastic Beach      album   
4                                            Gorillaz      album   
5                                          Demon Days      album   
6   New Gold (feat. Tame Impala and Bootie Brown) ...     single   
7                                     Humanz (Deluxe)      album   
8                   Cracker Island (feat. Thundercat)     single   
9                                          Demon Days      album  

# Data Exploration

Qui inizia la fase di esplorazione, essa comprenderà due parti. La prima sarà svolta su Pandas usando un subset, la seconda verrà fatta in PySpark utilizzando tutto il DataFrame.
Per prendere il subset si è pensato di utilizzare solo i brani che sono singoli, quindi non direttamente associati ad un album. Di seguito le numeriche.



In [ ]:
df.groupBy('Album_type').count().show()

+-----------+-----+
| Album_type|count|
+-----------+-----+
|      album|14926|
|compilation|  788|
|     single| 5004|
+-----------+-----+



### Pandas
Inizialmente andremo ad estrarre una serie di numeriche per capire l'ordine di grandezza del Dataframe,la struttura che ha, quanti artisti ci sono, quante canzoni e quali sono le distribuzioni delle variabili numeriche

In [ ]:
#Filtriamo per ottenere solo un subset di righe
df_pandas = df_pandas[df_pandas['Album_type']== 'single']

In [ ]:
print('Numero di righe :', df_pandas.shape[0])
print('Numero di colonne :', df_pandas.shape[1])

Numero di righe : 5004
Numero di colonne : 28


In [ ]:
#Vediamo, per singola variabile, il numero di campi nulli presenti nel Dataframe
df_pandas.isna().sum()

Unnamed: 0            0
Artist                0
Url_spotify           0
Track                 0
Album                 0
Album_type            0
Uri                   0
Danceability          0
Energy                0
Key                   0
Loudness              0
Speechiness           0
Acousticness          0
Instrumentalness      0
Liveness              0
Valence               0
Tempo                 0
Duration_ms           0
Url_youtube         144
Title               144
Channel             144
Views               144
Likes               152
Comments            157
Description         203
Licensed            144
official_video      144
Stream              154
dtype: int64

In [ ]:
#Informazioni generiche sul DataFrame, la struttura, il tipo per singola colonna, i nomi delle colonne
df_pandas.info()

<class 'pandas.core.frame.DataFrame'>
Index: 5004 entries, 2 to 20717
Data columns (total 28 columns):
 #   Column            Non-Null Count  Dtype  
---  ------            --------------  -----  
 0   Unnamed: 0        5004 non-null   int64  
 1   Artist            5004 non-null   object 
 2   Url_spotify       5004 non-null   object 
 3   Track             5004 non-null   object 
 4   Album             5004 non-null   object 
 5   Album_type        5004 non-null   object 
 6   Uri               5004 non-null   object 
 7   Danceability      5004 non-null   float64
 8   Energy            5004 non-null   float64
 9   Key               5004 non-null   float64
 10  Loudness          5004 non-null   float64
 11  Speechiness       5004 non-null   float64
 12  Acousticness      5004 non-null   float64
 13  Instrumentalness  5004 non-null   float64
 14  Liveness          5004 non-null   float64
 15  Valence           5004 non-null   float64
 16  Tempo             5004 non-null   float64
 17 

In [ ]:
#Con la funzione describe di Pandas possiamo iniziare a vedere quali sono le distribuzioni delle variabili e se ci sono valori nulli
df_pandas[['Danceability','Energy','Key','Loudness','Speechiness','Acousticness','Instrumentalness','Liveness','Valence','Tempo','Duration_ms','Views','Likes','Comments','Stream']].describe()

Danceability       Energy          Key     Loudness  Speechiness  \
count   5004.000000  5004.000000  5004.000000  5004.000000  5004.000000   
mean       0.665004     0.668292     5.474820    -6.518279     0.103867   
std        0.145717     0.187904     3.593802     3.356781     0.096274   
min        0.000000     0.003420     0.000000   -36.062000     0.000000   
25%        0.578750     0.554000     2.000000    -7.640250     0.040875   
50%        0.682500     0.692000     6.000000    -5.864000     0.061800   
75%        0.774000     0.812000     9.000000    -4.548000     0.128000   
max        0.975000     0.997000    11.000000     0.920000     0.885000   

       Acousticness  Instrumentalness     Liveness      Valence        Tempo  \
count   5004.000000       5004.000000  5004.000000  5004.000000  5004.000000   
mean       0.264644          0.042978     0.188559     0.530126   121.311118   
std        0.261604          0.162147     0.158349     0.231006    27.876180   
min        0.000006          0.000000     0.014500     0.000000     0.000000   
25%        0.048000          0.000000     0.095100     0.351000    99.549250   
50%        0.173000          0.000001     0.125000     0.535000   121.111500   
75%        0.417000          0.000343     0.227250     0.714000   137.926500   
max        0.996000          1.000000     0.984000     0.981000   236.059000   

        Duration_ms         Views         Likes      Comments        Stream  
count  5.004000e+03  4.860000e+03  4.852000e+03  4.847000e+03  4.850000e+03  
mean   2.091160e+05  8.269886e+07  7.136080e+05  2.715219e+04  1.016708e+08  
std    9.763285e+04  2.461023e+08  1.850603e+06  1.365045e+05  1.987213e+08  
min    6.012000e+04  2.800000e+01  0.000000e+00  0.000000e+00  6.574000e+03  
25%    1.668750e+05  1.374965e+06  2.356900e+04  5.305000e+02  9.343537e+06  
50%    1.976035e+05  1.132483e+07  1.411035e+05  3.084000e+03  3.330787e+07  
75%    2.320500e+05  6.328650e+07  6.178682e+05  1.533700e+04  1.000162e+08  
max    4.120258e+06  5.773798e+09  4.014767e+07  5.331537e+06  2.456205e+09

In [ ]:
# Numero di artisti, tracce e album distinti
print('Numero di artisti presenti: ', df_pandas['Artist'].nunique())
print('Numero di tracce presenti: ', df_pandas['Track'].nunique())
print('Numero di album presenti: ', df_pandas['Album'].nunique())

Numero di artisti presenti:  1355
Numero di tracce presenti:  4141
Numero di album presenti:  3958


In [ ]:
#Con questo grafico andiamo a visualizzare in maniera diretta la distribuzione dei valori nelle variabili numeriche che descrivono la singola canzone
numeric_col = ['Danceability','Energy','Key','Loudness','Speechiness','Acousticness','Instrumentalness','Liveness','Valence','Tempo']
create_interactive_hist(df_pandas, 'pandas', 'Distribuzione della frequenza', numeric_col)

In [ ]:
#Con questo grafico andiamo a visualizzare in maniera diretta la distribuzione dei valori nelle varibili numeriche relative all'engagment
eng_col = ['Duration_ms','Views','Likes','Comments','Stream']
create_interactive_hist(df_pandas, 'pandas', 'Distribuzione della frequenza', eng_col, color = 'red')

Da questa prima analisi esplorativa abbiamo compreso che:
- sono presenti valori nulli che verranno gestiti nella fase di cleaning
- che potrebbero esserci valori duplicati
- che le distribuzioni delle variabili numeriche seguono quasi tutti una gaussiana

### Spark
Adesso ripetiamo l'analisi utilizzando Pyspark su tutto il Dataframe

In [ ]:
print('Numero di righe :', df.count())
print('Numero di colonne :', len(df_pandas.columns))

Numero di righe : 20718
Numero di colonne : 28


In [ ]:
#Valori nulli per colonne
df.select([f.sum(f.col(c).isNull().cast("int")).alias(c) for c in df.columns]).show()

+---+------+-----------+-----+-----+----------+---+------------+------+---+--------+-----------+------------+----------------+--------+-------+-----+-----------+-----------+-----+-------+-----+-----+--------+-----------+--------+--------------+------+
|_c0|Artist|Url_spotify|Track|Album|Album_type|Uri|Danceability|Energy|Key|Loudness|Speechiness|Acousticness|Instrumentalness|Liveness|Valence|Tempo|Duration_ms|Url_youtube|Title|Channel|Views|Likes|Comments|Description|Licensed|official_video|Stream|
+---+------+-----------+-----+-----+----------+---+------------+------+---+--------+-----------+------------+----------------+--------+-------+-----+-----------+-----------+-----+-------+-----+-----+--------+-----------+--------+--------------+------+
|  0|     0|          0|    0|    0|         0|  0|           2|     2|  2|       2|          2|           2|               2|       2|      2|    2|          2|        470|  470|    470|  470|  541|     569|        876|     470|           470|

In [ ]:
df.printSchema()

root
 |-- _c0: integer (nullable = true)
 |-- Artist: string (nullable = true)
 |-- Url_spotify: string (nullable = true)
 |-- Track: string (nullable = true)
 |-- Album: string (nullable = true)
 |-- Album_type: string (nullable = true)
 |-- Uri: string (nullable = true)
 |-- Danceability: double (nullable = true)
 |-- Energy: double (nullable = true)
 |-- Key: double (nullable = true)
 |-- Loudness: double (nullable = true)
 |-- Speechiness: double (nullable = true)
 |-- Acousticness: double (nullable = true)
 |-- Instrumentalness: double (nullable = true)
 |-- Liveness: double (nullable = true)
 |-- Valence: double (nullable = true)
 |-- Tempo: double (nullable = true)
 |-- Duration_ms: double (nullable = true)
 |-- Url_youtube: string (nullable = true)
 |-- Title: string (nullable = true)
 |-- Channel: string (nullable = true)
 |-- Views: double (nullable = true)
 |-- Likes: double (nullable = true)
 |-- Comments: double (nullable = true)
 |-- Description: string (nullable = true)


In [ ]:
df.select('Danceability','Energy','Key','Loudness','Speechiness','Acousticness','Instrumentalness','Liveness','Valence','Tempo','Duration_ms','Views','Likes','Comments','Stream').describe().show()

+-------+-------------------+-------------------+------------------+------------------+-------------------+-------------------+-------------------+-------------------+------------------+------------------+------------------+-------------------+------------------+------------------+--------------------+
|summary|       Danceability|             Energy|               Key|          Loudness|        Speechiness|       Acousticness|   Instrumentalness|           Liveness|           Valence|             Tempo|       Duration_ms|              Views|             Likes|          Comments|              Stream|
+-------+-------------------+-------------------+------------------+------------------+-------------------+-------------------+-------------------+-------------------+------------------+------------------+------------------+-------------------+------------------+------------------+--------------------+
|  count|              20716|              20716|             20716|             20716| 

In [ ]:
df.select(f.countDistinct("Artist").alias('Numero artisti distinti')).show()
df.select(f.countDistinct("Track").alias('Numero brani distinti')).show()
df.select(f.countDistinct("Album").alias('Numero Album distinti')).show()

+-----------------------+
|Numero artisti distinti|
+-----------------------+
|                   2079|
+-----------------------+

+---------------------+
|Numero brani distinti|
+---------------------+
|                17841|
+---------------------+

+---------------------+
|Numero Album distinti|
+---------------------+
|                11937|
+---------------------+



In [ ]:
numeric_col = ['Danceability','Energy','Key','Loudness','Speechiness','Acousticness','Instrumentalness','Liveness','Valence','Tempo']
create_interactive_hist(df, 'spark', 'Distribuzione della frequenza', numeric_col)

In [ ]:
eng_col = ['Duration_ms','Views','Likes','Comments','Stream']
create_interactive_hist(df, 'spark', 'Distribuzione della frequenza', eng_col, color = 'red')

Questa seconda analisi ha confermato la prima, adesso si andrà a gestire alcune casistiche nella prossima fase

# Data Cleaning & Manipulation
In questa parte si andrà a fare pulizia del dato e a manipolarlo al fine di creare un dataframe utilizzabile nella parte di analisi.
Per le operazioni verrà spesso utilizzata la windows function, che consente, in modo ottimizzato, di lavorare con le partizioni in Spark


In [ ]:
#rinomino la colonna degli indici
df = df.withColumnRenamed('_c0', 'Index')

In [ ]:
df.select([f.sum(f.col(c).isNull().cast("int")).alias(c) for c in df.columns]).show()

+-----+------+-----------+-----+-----+----------+---+------------+------+---+--------+-----------+------------+----------------+--------+-------+-----+-----------+-----------+-----+-------+-----+-----+--------+-----------+--------+--------------+------+
|Index|Artist|Url_spotify|Track|Album|Album_type|Uri|Danceability|Energy|Key|Loudness|Speechiness|Acousticness|Instrumentalness|Liveness|Valence|Tempo|Duration_ms|Url_youtube|Title|Channel|Views|Likes|Comments|Description|Licensed|official_video|Stream|
+-----+------+-----------+-----+-----+----------+---+------------+------+---+--------+-----------+------------+----------------+--------+-------+-----+-----------+-----------+-----+-------+-----+-----+--------+-----------+--------+--------------+------+
|    0|     0|          0|    0|    0|         0|  0|           2|     2|  2|       2|          2|           2|               2|       2|      2|    2|          2|        470|  470|    470|  470|  541|     569|        876|     470|       

### Gestione Nulli

In [ ]:
num_col = ['Danceability','Energy','Key','Loudness','Speechiness','Acousticness','Instrumentalness','Liveness','Valence','Tempo', 'Duration_ms','Stream']
yt_video_string_col = ['Url_youtube','Title','Channel','Description']
bool_col = ['Licensed', 'official_video']
yt_video_num_col = ['Views','Likes','Comments']
df_clean = df
windowSpec  = Window.partitionBy("Artist")

#se la colonna numerica è nulla la imputo con il valore medio della colonna per artista
for col in num_col:
  df_clean = df_clean.withColumn(
      col,
      f.when(f.col(col).isNull(), f.avg(col).over(windowSpec)).otherwise(f.col(col))
  )

# se la colonna boolena è nulla allora consideremo false il valore
for col in bool_col:
  df_clean = df_clean.withColumn(col, f.when(f.col(col).isNull(), False).otherwise(f.col(col)))

# se il valore è null e abbiamo l'url di yt, quindi il video esiste, allora metto la media delle views per artista, se il video non esiste metto 0 views, altrimenti lascio il valore esistente
for col in yt_video_num_col:
  df_clean = df_clean.withColumn(col,f.when((~(f.col('Url_youtube').isNull())) & (f.col(col).isNull()), f.avg(col).over(windowSpec) ).otherwise(
      (f.when((f.col('Url_youtube').isNull()) & (f.col(col).isNull()), 0)).otherwise(f.col(col))
      ))

#per le colonne stringa da null passo ad 'assente'
for col in yt_video_string_col:
  df_clean = df_clean.withColumn(col, f.when(f.col(col).isNull(), 'Assente').otherwise(f.col(col)))

#gestione caso particolare in cui non abbiamo stream di spotify dell'artista. In questo caso assegneremo come valore il numero medio di visualizzazione della canzone per artista
df_clean = df_clean.withColumn('Stream', f.when(f.col('Stream').isNull(), f.avg('Views').over(windowSpec)).otherwise(f.col('Stream')))

#gestione caso particolare in cui non abbiamo il numero di commenti dei video dell'artista. In questo caso assegneremo come valore 0
df_clean = df_clean.withColumn('Comments', f.when(f.col('Comments').isNull(), f.lit(0)).otherwise(f.col('Comments')))


In [ ]:
df_clean.select([f.sum(f.col(c).isNull().cast("int")).alias(c) for c in df.columns]).show()

+-----+------+-----------+-----+-----+----------+---+------------+------+---+--------+-----------+------------+----------------+--------+-------+-----+-----------+-----------+-----+-------+-----+-----+--------+-----------+--------+--------------+------+
|Index|Artist|Url_spotify|Track|Album|Album_type|Uri|Danceability|Energy|Key|Loudness|Speechiness|Acousticness|Instrumentalness|Liveness|Valence|Tempo|Duration_ms|Url_youtube|Title|Channel|Views|Likes|Comments|Description|Licensed|official_video|Stream|
+-----+------+-----------+-----+-----+----------+---+------------+------+---+--------+-----------+------------+----------------+--------+-------+-----+-----------+-----------+-----+-------+-----+-----+--------+-----------+--------+--------------+------+
|    0|     0|          0|    0|    0|         0|  0|           0|     0|  0|       0|          0|           0|               0|       0|      0|    0|          0|          0|    0|      0|    0|    0|       0|          0|       0|       

In [ ]:
#rifaccio il print dello schema per essere sicuro che non ci siano stati, durante l'eliminazione dei null, errori per cui alcune colonne hanno cambiato type
df_clean.printSchema()

root
 |-- Index: integer (nullable = true)
 |-- Artist: string (nullable = true)
 |-- Url_spotify: string (nullable = true)
 |-- Track: string (nullable = true)
 |-- Album: string (nullable = true)
 |-- Album_type: string (nullable = true)
 |-- Uri: string (nullable = true)
 |-- Danceability: double (nullable = true)
 |-- Energy: double (nullable = true)
 |-- Key: double (nullable = true)
 |-- Loudness: double (nullable = true)
 |-- Speechiness: double (nullable = true)
 |-- Acousticness: double (nullable = true)
 |-- Instrumentalness: double (nullable = true)
 |-- Liveness: double (nullable = true)
 |-- Valence: double (nullable = true)
 |-- Tempo: double (nullable = true)
 |-- Duration_ms: double (nullable = true)
 |-- Url_youtube: string (nullable = true)
 |-- Title: string (nullable = true)
 |-- Channel: string (nullable = true)
 |-- Views: double (nullable = true)
 |-- Likes: double (nullable = true)
 |-- Comments: double (nullable = true)
 |-- Description: string (nullable = true

In [ ]:
df_clean.show()

+-----+-----------+--------------------+--------------------+--------------------+----------+--------------------+------------+------+----+--------+-----------+------------+----------------+--------+-------+-------+-----------+--------------------+-------------------------+-------------------------+------------+---------+--------+--------------------------------+--------+--------------+------------+
|Index|     Artist|         Url_spotify|               Track|               Album|Album_type|                 Uri|Danceability|Energy| Key|Loudness|Speechiness|Acousticness|Instrumentalness|Liveness|Valence|  Tempo|Duration_ms|         Url_youtube|                    Title|                  Channel|       Views|    Likes|Comments|                     Description|Licensed|official_video|      Stream|
+-----+-----------+--------------------+--------------------+--------------------+----------+--------------------+------------+------+----+--------+-----------+------------+----------------+----

### Verifica duplicati

In [ ]:
#check duplicati, verifico che non ci siano canzoni con lo stesso artista e che fanno riferimento allo stesso album
df_app = df_clean
df_app = df_app.withColumn('check', f.concat(f.col('Artist'), f.col('Track'), f.col('Album')))
windowSpec  = Window.partitionBy("check").orderBy("check")
df_app.withColumn("row_count", f.count("*").over(windowSpec)).filter(f.col("row_count") > 1).show()

+-----+------+-----------+-----+-----+----------+---+------------+------+---+--------+-----------+------------+----------------+--------+-------+-----+-----------+-----------+-----+-------+-----+-----+--------+-----------+--------+--------------+------+-----+---------+
|Index|Artist|Url_spotify|Track|Album|Album_type|Uri|Danceability|Energy|Key|Loudness|Speechiness|Acousticness|Instrumentalness|Liveness|Valence|Tempo|Duration_ms|Url_youtube|Title|Channel|Views|Likes|Comments|Description|Licensed|official_video|Stream|check|row_count|
+-----+------+-----------+-----+-----+----------+---+------------+------+---+--------+-----------+------------+----------------+--------+-------+-----+-----------+-----------+-----+-------+-----+-----+--------+-----------+--------+--------------+------+-----+---------+
+-----+------+-----------+-----+-----+----------+---+------------+------+---+--------+-----------+------------+----------------+--------+-------+-----+-----------+-----------+-----+-------+-

In [ ]:
#tutte le canzoni di un'artista hanno un URL diverso su spotify
df_app = df_clean
df_app = df_app.withColumn('check', f.concat(f.col('Artist'), f.col('Uri')))
windowSpec = Window.partitionBy("check").orderBy("check")
df_app.withColumn("row_count", f.count("*").over(windowSpec)).filter(f.col("row_count") > 1).show(truncate=False)

+-----+------+-----------+-----+-----+----------+---+------------+------+---+--------+-----------+------------+----------------+--------+-------+-----+-----------+-----------+-----+-------+-----+-----+--------+-----------+--------+--------------+------+-----+---------+
|Index|Artist|Url_spotify|Track|Album|Album_type|Uri|Danceability|Energy|Key|Loudness|Speechiness|Acousticness|Instrumentalness|Liveness|Valence|Tempo|Duration_ms|Url_youtube|Title|Channel|Views|Likes|Comments|Description|Licensed|official_video|Stream|check|row_count|
+-----+------+-----------+-----+-----+----------+---+------------+------+---+--------+-----------+------------+----------------+--------+-------+-----+-----------+-----------+-----+-------+-----+-----+--------+-----------+--------+--------------+------+-----+---------+
+-----+------+-----------+-----+-----+----------+---+------------+------+---+--------+-----------+------------+----------------+--------+-------+-----+-----------+-----------+-----+-------+-

In [ ]:
#le stesse canzoni, fatte in collaborazione tra più artisti, vengono segnate per ogni artista separatamente
windowSpec = Window.partitionBy("Uri").orderBy("Uri")
df_app.withColumn("row_count", f.count("*").over(windowSpec)).filter(f.col("row_count") > 1).show(truncate=False)

+-----+------------------------+------------------------------------------------------+-----------------------------------------------------------------+-------------------------------------+----------+------------------------------------+------------+------+---+--------+-----------+------------+----------------+--------+-------+-------+-----------+-------------------------------------------+---------------------------------------------------------------------------------------+------------------------+------------+---------+--------+----------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

In [ ]:
# i duplicati fanno riferimento a canzoni presenti su spotify molto simili (es. remix, radio edit ecc..) ma che fanno riferimento a un unico video youtube
df_app = df_clean
df_app = df_app.withColumn('check', f.concat(f.col('Artist'), f.col('Url_youtube')))
windowSpec  = Window.partitionBy("check").orderBy("check")
df_app.withColumn("row_count", f.count("*").over(windowSpec)).filter(f.col("row_count") > 1).show(truncate=False)

+-----+---------------------+------------------------------------------------------+----------------------------------------------------------+----------------------------------------------------------+----------+------------------------------------+------------+------+----+--------+-----------+------------+----------------+--------+-------+-------+-----------+-------------------------------------------+----------------------------------------------------------------------------------------------+---------------------+------------+------------------+--------+---------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

In [ ]:
#Creo tre colonne, una per avere un id canzone artista, una per avere il numero totale di ascolti contando le due piattaforme
#e un'altra che mi indica quali sono "hit" e quali no in base alla piattaforma (si considera hit la canzone con più di 1 miliardo di ascolti)
df_single_song = df_clean.withColumn('All_reproduction', f.col('Stream')+f.col('Views'))
df_single_song = df_single_song.withColumn('Song_id', f.concat(f.col('Track'), f.lit(" - ") ,f.col('Artist'))).\
  withColumn('is_hit_spotify', f.col('Stream') > 1000000000).\
  withColumn('is_hit_yt', f.col('Views') > 1000000000)


# Aggregation

In questa sezione andremo a creare un dataset aggregato in modo da avere tutte le informazioni che riterremo interessanti per ogni artista

In [ ]:
#Per ogni artista mi calcolo il numero di ascolti per piattaforma e successivamente il medio sul numero di canzoni presenti
windowSpec  = Window.partitionBy("Artist")
df_aggr = df_clean.withColumn("n_spotify_song", f.count("Uri").over(windowSpec)).\
  withColumn("n_spotify_stream", f.sum("Stream").over(windowSpec)).\
  withColumn("n_yt_song", f.count("Url_youtube").over(windowSpec)).\
  withColumn("n_yt_stream", f.sum("Views").over(windowSpec)).\
  withColumn("n_all_stream", f.col('n_spotify_stream') + f.col('n_yt_stream')).\
  withColumn("n_url_distinct", f.col('n_yt_song')+f.col('n_spotify_song'))

df_aggr = df_aggr.select("Artist", "n_spotify_song", "n_spotify_stream", "n_yt_song", "n_yt_stream", 'n_all_stream', 'n_url_distinct').dropDuplicates()

df_aggr = df_aggr.withColumn('Mean_spotify_stream', f.col('n_spotify_stream')/f.col('n_spotify_song')).\
  withColumn('Mean_yt_stream', f.col('n_yt_stream')/f.col('n_yt_song')).\
  withColumn('Mean_all_stream', f.col('n_all_stream')/f.col('n_url_distinct'))

# Analysis and visualization
Per la parte di analisi utilizeremo Pandas. Le analisi puntano a comprendere quali siano le canzoni e gli artisti più riprodotti e ad individuare delle possibili correlazioni tra le variabili che descrivono la canzone e il successo che hanno

In [ ]:
df_aggr_pandas = df_aggr.toPandas()
df_single_song_pandas = df_single_song.toPandas()

Inizialmente andiamo a vedere quali sono le 10 canzoni più ascoltate su Youtube, Spotify e in generale.
Il grafico è dinamico, è possibile selezionare la variabile di riferimento che si preferisce

In [ ]:
y_col = ['Views', 'Stream','All_reproduction']
x_col = ['Song_id']
df_song_noDupl = df_single_song_pandas.drop_duplicates(['Uri', 'Url_youtube'])
create_interactive_bar(df_song_noDupl, x_col, y_col, 'Top 10 most played songs', 'black')

Inizialmente andiamo a vedere quali sono i 10 artisti più ascoltati su Youtube, Spotify e in generale.
Per farlo prenderemo i valori medi degli ascolti in modo da non essere influenzati dal numero di brani che gli artisti hanno pubblicato.
Il grafico è dinamico, è possibile selezionare la variabile di riferimento che si preferisce

In [ ]:
y_col = ['Mean_all_stream', 'Mean_yt_stream','Mean_spotify_stream']
x_col = ['Artist']
create_interactive_bar(df_aggr_pandas, x_col, y_col, 'Top 10 most played artist', 'green')

Con lo scatterplot andiamo ad investigare se è possibile visualizzare qualche tipo di correlazione tra le variabili che descrivono le caratteristiche delle canzoni e quanto hanno avuto successo (rappresentato dal numero di ascolti) sulle piattaforme o in generale

In [ ]:
y_col = ['Danceability','Energy','Key','Loudness','Speechiness','Acousticness','Instrumentalness','Liveness','Valence','Tempo', 'Duration_ms']

x_col = ['Views', 'Stream','All_reproduction']

create_interactive_scat(df_single_song_pandas, x_col, y_col, 'Scatter plot', 'orange')

Dallo scatterplot non sembrano emerse correlazioni evidenti, per confermare questo utilizzeremo una matrice di correlazione

In [ ]:
# Calcola la matrice di correlazione
df_corr = df_single_song_pandas[['Danceability','Energy','Key','Loudness','Speechiness','Acousticness','Instrumentalness','Liveness','Valence','Tempo', 'Duration_ms','Views', 'Stream','All_reproduction', 'Comments', 'Likes', 'is_hit_spotify', 'is_hit_yt']]
corr_matrix = df_corr.corr()

# Crea la heatmap della matrice di correlazione
fig = px.imshow(corr_matrix, text_auto=True, title="Matrice di Correlazione")
fig.show()

Da questa prima analisi non abbiamo ottenuto risultati importanti, quindi proviamo a modificare leggermente l'analisi andando a vedere, tramite un boxplot, le distribuzioni delle hit, rispetto alle non hit, per vedere se, andando a confrontare questi parametri troviamo qualche differenza. L'analisi verrà ripetuta sulle hit per entrambe le piattaforme separatamente

In [ ]:
cols = ['Danceability','Energy','Key','Loudness','Speechiness','Acousticness','Instrumentalness','Liveness','Valence','Tempo']
create_interactive_boxplot(df_single_song_pandas, cols, 'is_hit_spotify', 'Hit vs No-Hit Spotify')
create_interactive_boxplot(df_single_song_pandas, cols, 'is_hit_yt', 'Hit vs No-Hit YouTube')

Da questa analisi si può evincere che le canzoni classificate come "hit" hanno valori un pò più alti di dancebility, energy e più bassi di acousticness.

### Modello di classificazione

Creiamo un modello di classificazione per cercare di classificare le canzoni utilizzando i valori delle variabili che la descrivono.

Per svolgere questo task come modello prenderemo un random forest classifier in quanto robusto contro l'overfitting e buono nella gestione di feature non rilevanti.
Come variabile target creeremo una colonna che indica se una canzone è popolare, per farlo abbiamo preso come riferimento i valori delle Views, che devono essere maggiori di 10M per Youtube; per Spotify il valore soglia delle Stream è 50M. Questi valori sono stati scelti per ottenere un dataset abbastanza bilanciato.

In [ ]:
df_model_yt = df_single_song.withColumn('is_popular', f.col('Views') > 10000000).toPandas()
print(f"Percentule True sul totale: {df_model_yt['is_popular'].sum()/len(df_model_yt['is_popular'])}")

Percentule True sul totale: 0.5414615310358143


In [ ]:
df_model_spotify = df_single_song.withColumn('is_popular', f.col('Stream') > 50000000).toPandas()
print(f"Percentule True sul totale: {df_model_spotify['is_popular'].sum()/len(df_model_spotify['is_popular'])}")

Percentule True sul totale: 0.5001448016217782


In [ ]:
feature_list = ['Danceability','Energy','Key','Loudness','Speechiness','Acousticness','Instrumentalness','Liveness','Valence','Tempo', 'Duration_ms']
random_forest(df_model_yt, feature_list, 'is_popular')

Accuratezza: 0.6631274131274131 

              precision    recall  f1-score   support

       False       0.65      0.54      0.59      1872
        True       0.67      0.76      0.71      2272

    accuracy                           0.66      4144
   macro avg       0.66      0.65      0.65      4144
weighted avg       0.66      0.66      0.66      4144



In [ ]:
feature_list = ['Danceability','Energy','Key','Loudness','Speechiness','Acousticness','Instrumentalness','Liveness','Valence','Tempo', 'Duration_ms']
random_forest(df_model_spotify, feature_list, 'is_popular')

Accuratezza: 0.6298262548262549 

              precision    recall  f1-score   support

       False       0.63      0.64      0.63      2070
        True       0.63      0.62      0.63      2074

    accuracy                           0.63      4144
   macro avg       0.63      0.63      0.63      4144
weighted avg       0.63      0.63      0.63      4144



Leggendo le metriche, il modello si comporta discretamente bene, non è un modello eccellente ma sui dati che abbiamo è un risultato soddisfacente, in quanto, se dovessimo alzare (o abbassare) la soglia per avere un flag True nella variabile Target, le proporzioni sarebbero squilibrate e si avrebbe overfitting, in quanto, pur alzandosi l'accuracy, si noterebbero anomalie nelle altre metriche.

### Conclusioni

Da questa analisi non siamo riusciti a trovare delle correlazioni molto forti ed evidenti e questo può essere legato sia alla grandezza del dataset, in quanto i dati non sono tantissimi che al tipo di informazioni, a volte inerenti solo la singola canzone e non un contesto più ampio.
Di seguito alcuni possibili next step per un'analisi più approfondita:
- aumento del numero delle righe, prendere un numero più ampio di canzoni
- aumento delle informazioni
  - estrarre informazioni come la data di uscita del brano per capire l'arco temporale della raccolta dei dati e gli anni in cui è stato composto
  - avere come parametro anche il numero di follower dell'artista per poter anche calibrare la popolarità dell'artista che, sicuramente influenza
  - avere dati anche di altre piattaforme come amazon music e soprattutto tiktok, che negli ultimi anni influenza tantissimo il mercato musicale
  - conoscere l'etichetta dell'artista che distribuisce le canzoni

Con queste informazioni aggiuntive si potrebbero fare analisi più specifiche per ogni artista e per ogni piattaforme. Si potrebbe riflettere su analisi di come un'artista sia cresciuto aumentando gli ascolti e capire veramente tutti i fattori che influenzano questo, in quanto, non basta fare una bella canzone per avere successo e le correlazioni possono essere tante